In [1]:
import sqlite3
# import os.path
import hashlib
import pandas as pd
import numpy as np


db = './../data/daf06fb3ab69f27bd681a63311722181.db'
db = './test.db'

conn = sqlite3.connect(db)
df = pd.read_sql_query("SELECT * FROM loadsonly;", conn)
conn.close()# close db

df['datetime'] = pd.to_datetime(df['datetime'])
df.sort_values(by='datetime',ascending=True);


In [2]:
df['dp'] = df['demand'] - df['demand'].shift(1)
df['dp+'] = [0-x if x <=0 else 0 for x in df['dp']]
df['dp-'] = [x if x >=0 else 0 for x in df['dp']]

df['dp'] = df['demand'] - df['demand'].shift(1)
for x in range(1,len(df)):
    df.loc[x,'dp'] = df.loc[x,'demand'] -  df.loc[x-1,'demand']
    if df.loc[x,'dp'] > 0:
        df.loc[x,'dp+'] = df.loc[x,'dp']
        df.loc[x,'dp-'] = 0
    else:
        df.loc[x,'dp-'] = 0-df.loc[x,'dp']
        df.loc[x,'dp+'] = 0

In [3]:
# add user defined loads
user_loads = {'modem':10,'rPi':4}
baseload = 0
for user_load in user_loads:
    df.loc[:,user_load]  = user_loads[user_load]
    baseload = baseload + user_loads[user_load]
#     df.loc[:,] = np.array([df['demand'].min()] * len(df))


In [4]:
# find baseload and determine remaining unkwown profile
df.loc[:,'baseload'] = np.array([df['demand'].min()-baseload] * len(df))
df.loc[:,'unknown'] = df.loc[:,'demand'] - df.loc[:,'baseload']-baseload


In [5]:
# df[pd.isnull(df).any(axis=1)]

In [6]:
def left_round(number,precision=2):
    rem = number

    d = len(str(number))
    while(round(rem,d) == round(number,d)):
        rem = round(number,d-precision)
        d = d -1
        
    i = 0
    while(rem > 10**precision):
        rem = round(rem / 10,0)
        i = i +1
#         print(rem*(10**i))
        if i > 100:
            break
    return rem*(10**i)

left_round(00.00034564,3)

left_round(122431234.00034564,3)

# left_round(123456)

122000000.0

In [7]:
#find square loads
loads = dict()

for x in range(1,len(df)):
    #filter for dP+ with minimim power
    if df.loc[x,'dp+'] > 100:
        print(' ') #new line in output
        print ('start dp>100:',df.loc[x,'datetime'],'start P:',df.loc[x-1,'unknown'],'dP+:' ,df.loc[x,'dp+'])
        
        #look forwar in time to see how long load remains on
        for y in range(x+1,len(df)):
            #find dP- of same/simulair size 
            if df.loc[y,'dp-'] > 0.9 *df.loc[x,'dp+'] and df.loc[y,'dp-'] < 1.1 *df.loc[x,'dp+']:
                print ('stop dP-:',df.loc[y,'datetime'],'dP-:' ,df.loc[y,'dp-'])
                break
            # check if does not drop below start power (this means is must have been turned of)    
            if df.loc[y,'unknown'] <= df.loc[x-1,'unknown']:
                print ('stop demand:',df.loc[x,'datetime'] ,df.loc[y,'unknown'], ' <= ',df.loc[x-1,'unknown'])
                break
        
        print(x,y,(df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).mean())
        
        # calculate key parameters
        mean = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).mean()
        max = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).max()
        min = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).min()
        std = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).std()
        time = pd.Timedelta(pd.to_datetime(df['datetime'][y])-pd.to_datetime(df['datetime'][x]))
        noise = df.loc[x:y-1,'dp'].abs().mean()
        
        print('mean load:',mean)
        print('max load:',max)
        print('std load:',std)
        print('noise:',noise)
        print('time past:',time)


        print('found profile from ',df.loc[x-1,'datetime'],'to',df.loc[y,'datetime'])
        profile = list(df.loc[x-1:y,'unknown']-df.loc[x-1,'unknown'])
        print(profile)
        
        
#         plt.plot(range(x,y),profile)
#         plt.title('A simple chirp')
#         plt.show()
#         break
        try:
            #drop loads which do not have a square looking profile.
            if (std/mean > 0.1):
                print('dropped because of large std:',std/mean)
                continue

            #drop loads which do not have odd start compared to mean
            if( abs(mean-df.loc[x,'dp+'])/df.loc[x,'dp+'] > 0.2):    
                print('dropped because large difference between mean and start dp+:',abs(mean-df.loc[x,'dp+'])/df.loc[x,'dp+'])
                continue
        except:
            print('Something went wrong in analysing found load, dropping ....')
            continue
#         print('hist:',df.hist(bins=10))
        
        # save this load to the distionairy (group by 'fingerprint')
        fingerprint = str(int(round(mean,-2)))+'_'#+str(int(left_round(df.loc[x,'dp+'],2)))
        temp = {'index':{'start':x,'stop':y},'time':time,'mean':mean,'max':max,'profile':profile}
        try:
            loads[fingerprint][len(loads[fingerprint])] = temp
        except:
            loads[fingerprint] = {0:temp}
            df[fingerprint] = 0 #add new colum to the dataframe before inserting found loads (only on first occurance!)
        
        df.loc[x:y-1,fingerprint] = profile[1:-1]
        df.loc[x:y-1,'unknown'] = df.loc[x:y-1,'unknown'] - profile[1:-1]
        print('Saved with fingerprint:',fingerprint)



 
start dp>100: 2017-09-21 19:32:09 start P: 173.0 dP+: 133.0
stop dP-: 2017-09-21 20:15:10 dP-: 120.0
149 409 230.33076923076922
mean load: 230.33076923076922
max load: 1071.0
std load: 285.376277743999
noise: 8.696153846153846
time past: 0 days 00:43:01
found profile from  2017-09-21 19:31:49 to 2017-09-21 20:15:10
[0.0, 133.0, 133.0, 179.0, 179.0, 180.0, 180.0, 181.0, 181.0, 179.0, 179.0, 179.0, 179.0, 169.0, 169.0, 170.0, 170.0, 168.0, 168.0, 168.0, 168.0, 167.0, 167.0, 167.0, 167.0, 168.0, 168.0, 167.0, 167.0, 172.0, 172.0, 173.0, 173.0, 173.0, 173.0, 160.0, 160.0, 160.0, 160.0, 161.0, 161.0, 155.0, 155.0, 154.0, 154.0, 152.0, 152.0, 149.0, 149.0, 161.0, 161.0, 969.0, 969.0, 970.0, 970.0, 1071.0, 1071.0, 1069.0, 1069.0, 1068.0, 1068.0, 1002.0, 1002.0, 1001.0, 1001.0, 996.0, 996.0, 990.0, 990.0, 989.0, 989.0, 990.0, 990.0, 992.0, 992.0, 988.0, 988.0, 983.0, 983.0, 982.0, 982.0, 174.0, 174.0, 174.0, 174.0, 174.0, 174.0, 173.0, 173.0, 175.0, 175.0, 175.0, 175.0, 175.0, 175.0, 175.0, 

stop demand: 2017-09-22 04:01:24 2.0  <=  8.0
3227 3411 304.0
mean load: 304.0
max load: 2032.0
std load: 410.02878747397364
noise: 51.60326086956522
time past: 0 days 00:30:27
found profile from  2017-09-22 04:01:05 to 2017-09-22 04:31:51
[0.0, 108.0, 108.0, 107.0, 107.0, 110.0, 110.0, 109.0, 109.0, 105.0, 105.0, 102.0, 102.0, 98.0, 98.0, 95.0, 95.0, 142.0, 142.0, 142.0, 142.0, 142.0, 142.0, 213.0, 213.0, 224.0, 224.0, 1059.0, 1059.0, 1059.0, 1059.0, 1077.0, 1077.0, 1075.0, 1075.0, 1084.0, 1084.0, 1080.0, 1080.0, 1089.0, 1089.0, 1092.0, 1092.0, 229.0, 229.0, 230.0, 230.0, 224.0, 224.0, 223.0, 223.0, 230.0, 230.0, 2032.0, 2032.0, 2024.0, 2024.0, 230.0, 230.0, 230.0, 230.0, 2014.0, 2014.0, 228.0, 228.0, 229.0, 229.0, 228.0, 228.0, 229.0, 229.0, 229.0, 229.0, 229.0, 229.0, 229.0, 229.0, 229.0, 229.0, 228.0, 228.0, 181.0, 181.0, 176.0, 176.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 169.0, 1

time past: 0 days 00:24:49
found profile from  2017-09-22 12:17:26 to 2017-09-22 12:42:35
[0.0, 108.0, 110.0, 107.0, 110.0, 108.0, 103.0, 100.0, 97.0, 95.0, 93.0, 92.0, 92.0, 92.0, 90.0, 89.0, 89.0, 89.0, 89.0, 89.0, 89.0, 89.0, 88.0, 89.0, 90.0, 89.0, 89.0, 89.0, 89.0, 90.0, 90.0, 90.0, 91.0, 90.0, 90.0, 90.0, 90.0, 91.0, 90.0, 91.0, 90.0, 90.0, 91.0, 89.0, 91.0, 90.0, 90.0, 90.0, 90.0, 89.0, 89.0, 89.0, 90.0, 90.0, 89.0, 89.0, 91.0, 89.0, 89.0, 89.0, 89.0, 89.0, 89.0, 87.0, 88.0, 90.0, 89.0, 88.0, 88.0, 88.0, 88.0, 89.0, 1.0, 1.0, 1.0, 2.0, 0.0]
dropped because of large std: 0.24310776221701963
 
start dp>100: 2017-09-22 13:28:54 start P: 2.0 dP+: 107.0
stop demand: 2017-09-22 13:28:54 2.0  <=  2.0
6058 6130 88.83333333333333
mean load: 88.83333333333333
max load: 109.0
std load: 15.702336777743948
noise: 3.513888888888889
time past: 0 days 00:23:49
found profile from  2017-09-22 13:28:34 to 2017-09-22 13:52:43
[0.0, 107.0, 109.0, 107.0, 109.0, 106.0, 102.0, 99.0, 98.0, 94.0, 93.0, 9

start dp>100: 2017-09-22 19:19:37 start P: 503.0 dP+: 2019.0
stop dP-: 2017-09-22 19:29:33 dP-: 2038.0
7118 7148 2003.1666666666667
mean load: 2003.1666666666667
max load: 2025.0
std load: 13.923642342862516
noise: 76.36666666666666
time past: 0 days 00:09:56
found profile from  2017-09-22 19:19:17 to 2017-09-22 19:29:33
[0.0, 2019.0, 2015.0, 1995.0, 1980.0, 1985.0, 1974.0, 1977.0, 1987.0, 2012.0, 2007.0, 2011.0, 2017.0, 2017.0, 2006.0, 2003.0, 2010.0, 2003.0, 2012.0, 2012.0, 2011.0, 2025.0, 2009.0, 1972.0, 1997.0, 2002.0, 2005.0, 2009.0, 2014.0, 2002.0, 2007.0, -31.0]
Saved with fingerprint: 2000_
 
start dp>100: 2017-09-22 19:51:43 start P: 81.0 dP+: 2048.0
stop dP-: 2017-09-22 20:06:56 dP-: 2054.0
7215 7261 2047.0652173913043
mean load: 2047.0652173913043
max load: 2120.0
std load: 12.637514126006907
noise: 50.67391304347826
time past: 0 days 00:15:13
found profile from  2017-09-22 19:51:23 to 2017-09-22 20:06:56
[0.0, 2048.0, 2049.0, 2046.0, 2048.0, 2055.0, 2055.0, 2050.0, 2044.0, 

start dp>100: 2017-09-23 07:41:49 start P: 60.0 dP+: 1744.0
stop dP-: 2017-09-23 07:42:29 dP-: 1742.0
9361 9363 1743.0
mean load: 1743.0
max load: 1744.0
std load: 1.4142135623730951
noise: 873.0
time past: 0 days 00:00:40
found profile from  2017-09-23 07:41:29 to 2017-09-23 07:42:29
[0.0, 1744.0, 1742.0, 0.0]
Saved with fingerprint: 1700_
 
start dp>100: 2017-09-23 07:43:28 start P: 21.0 dP+: 169.0
stop dP-: 2017-09-23 07:43:48 dP-: 177.0
9366 9367 169.0
mean load: 169.0
max load: 169.0
std load: nan
noise: 169.0
time past: 0 days 00:00:20
found profile from  2017-09-23 07:43:08 to 2017-09-23 07:43:48
[0.0, 169.0, -8.0]
Saved with fingerprint: 200_
 
start dp>100: 2017-09-23 07:44:08 start P: 13.0 dP+: 1739.0
stop dP-: 2017-09-23 07:44:28 dP-: 1739.0
9368 9369 1739.0
mean load: 1739.0
max load: 1739.0
std load: nan
noise: 1739.0
time past: 0 days 00:00:20
found profile from  2017-09-23 07:43:48 to 2017-09-23 07:44:28
[0.0, 1739.0, 0.0]
Saved with fingerprint: 1700_
 
start dp>100: 20

...

max load: 579.0
std load: 84.46892392314705
noise: 56.85294117647059
time past: 0 days 00:05:38
found profile from  2017-09-26 19:19:41 to 2017-09-26 19:25:29
[0.0, 427.0, 155.0, 176.0, 180.0, 175.0, 174.0, 174.0, 397.0, 330.0, 306.0, 267.0, 287.0, 281.0, 278.0, 281.0, 279.0, 276.0, 277.0, 274.0, 274.0, 273.0, 275.0, 275.0, 274.0, 274.0, 579.0, 273.0, 390.0, 340.0, 353.0, 349.0, 356.0, 357.0, 359.0, -51.0]
dropped because of large std: 0.28733801034387185
 
start dp>100: 2017-09-26 19:21:01 start P: 405.0 dP+: 223.0
stop demand: 2017-09-26 19:21:01 180.0  <=  405.0
30744 30771 142.07407407407408
mean load: 142.07407407407408
max load: 405.0
std load: 66.62404620528186
noise: 44.55555555555556
time past: 0 days 00:04:28
found profile from  2017-09-26 19:20:51 to 2017-09-26 19:25:29
[0.0, 223.0, 156.0, 132.0, 93.0, 113.0, 107.0, 104.0, 107.0, 105.0, 102.0, 103.0, 100.0, 100.0, 99.0, 101.0, 101.0, 100.0, 100.0, 405.0, 99.0, 216.0, 166.0, 179.0, 175.0, 182.0, 183.0, 185.0, -225.0]
dropped 

stop demand: 2017-09-27 08:42:06 2.0  <=  3.0
35586 35731 90.24137931034483
mean load: 90.24137931034483
max load: 109.0
std load: 5.260275476084039
noise: 1.3448275862068966
time past: 0 days 00:23:59
found profile from  2017-09-27 08:41:56 to 2017-09-27 09:06:05
[0.0, 107.0, 109.0, 109.0, 108.0, 107.0, 108.0, 108.0, 109.0, 106.0, 105.0, 101.0, 99.0, 98.0, 97.0, 96.0, 94.0, 94.0, 92.0, 92.0, 91.0, 91.0, 92.0, 91.0, 91.0, 90.0, 89.0, 89.0, 89.0, 88.0, 88.0, 88.0, 88.0, 89.0, 88.0, 88.0, 88.0, 89.0, 89.0, 88.0, 88.0, 88.0, 88.0, 88.0, 88.0, 89.0, 90.0, 89.0, 89.0, 90.0, 89.0, 89.0, 89.0, 88.0, 89.0, 90.0, 89.0, 89.0, 89.0, 90.0, 90.0, 90.0, 89.0, 90.0, 88.0, 89.0, 89.0, 89.0, 90.0, 90.0, 90.0, 90.0, 90.0, 90.0, 90.0, 90.0, 90.0, 90.0, 89.0, 88.0, 89.0, 89.0, 88.0, 89.0, 88.0, 88.0, 88.0, 88.0, 89.0, 88.0, 89.0, 89.0, 89.0, 89.0, 88.0, 89.0, 90.0, 89.0, 89.0, 88.0, 88.0, 89.0, 89.0, 88.0, 88.0, 89.0, 88.0, 89.0, 89.0, 88.0, 89.0, 88.0, 88.0, 88.0, 87.0, 88.0, 87.0, 87.0, 86.0, 87.0, 88.0

max load: 459.0
std load: 178.172294890835
noise: 152.33333333333334
time past: 0 days 00:00:59
found profile from  2017-09-27 16:21:34 to 2017-09-27 16:22:43
[0.0, 174.0, 459.0, 24.0, 23.0, 11.0, 18.0, -1494.0]
dropped because of large std: 1.5078050343371086
 
start dp>100: 2017-09-27 16:21:54 start P: 1762.0 dP+: 285.0
stop demand: 2017-09-27 16:21:54 1612.0  <=  1762.0
38365 38366 285.0
mean load: 285.0
max load: 285.0
std load: nan
noise: 285.0
time past: 0 days 00:00:10
found profile from  2017-09-27 16:21:44 to 2017-09-27 16:22:04
[0.0, 285.0, -150.0]
Saved with fingerprint: 300_
 
start dp>100: 2017-09-27 17:18:58 start P: 36.0 dP+: 143.0
stop demand: 2017-09-27 17:18:58 32.0  <=  36.0
38710 38929 211.84018264840182
mean load: 211.84018264840182
max load: 1813.0
std load: 367.0546881133949
noise: 40.91324200913242
time past: 0 days 00:36:15
found profile from  2017-09-27 17:18:48 to 2017-09-27 17:55:13
[0.0, 143.0, 110.0, 109.0, 110.0, 110.0, 110.0, 111.0, 109.0, 108.0, 107.0, 

stop demand: 2017-09-27 22:08:20 6.0  <=  25.0
40459 40605 75.56164383561644
mean load: 75.56164383561644
max load: 112.0
std load: 10.25803140537462
noise: 1.7191780821917808
time past: 0 days 00:24:10
found profile from  2017-09-27 22:08:10 to 2017-09-27 22:32:30
[0.0, 112.0, 111.0, 110.0, 111.0, 109.0, 112.0, 111.0, 109.0, 109.0, 106.0, 103.0, 102.0, 82.0, 81.0, 78.0, 76.0, 82.0, 81.0, 81.0, 79.0, 79.0, 74.0, 73.0, 73.0, 72.0, 71.0, 73.0, 71.0, 71.0, 71.0, 72.0, 72.0, 71.0, 72.0, 71.0, 71.0, 71.0, 70.0, 70.0, 70.0, 71.0, 71.0, 71.0, 72.0, 71.0, 71.0, 71.0, 73.0, 71.0, 72.0, 72.0, 71.0, 72.0, 72.0, 73.0, 74.0, 73.0, 73.0, 74.0, 73.0, 74.0, 72.0, 74.0, 73.0, 74.0, 74.0, 73.0, 73.0, 74.0, 73.0, 74.0, 74.0, 73.0, 73.0, 73.0, 73.0, 74.0, 73.0, 73.0, 73.0, 74.0, 74.0, 73.0, 73.0, 73.0, 73.0, 72.0, 72.0, 72.0, 73.0, 73.0, 74.0, 73.0, 74.0, 73.0, 73.0, 73.0, 72.0, 72.0, 72.0, 72.0, 72.0, 73.0, 74.0, 72.0, 72.0, 72.0, 73.0, 73.0, 71.0, 73.0, 73.0, 71.0, 73.0, 72.0, 72.0, 71.0, 71.0, 71.0, 73

time past: 0 days 00:24:09
found profile from  2017-09-28 07:48:44 to 2017-09-28 08:13:03
[0.0, 110.0, 109.0, 110.0, 110.0, 110.0, 111.0, 111.0, 109.0, 109.0, 107.0, 104.0, 102.0, 100.0, 100.0, 98.0, 96.0, 96.0, 95.0, 94.0, 93.0, 93.0, 92.0, 92.0, 92.0, 91.0, 90.0, 90.0, 89.0, 89.0, 90.0, 91.0, 90.0, 90.0, 90.0, 90.0, 90.0, 90.0, 90.0, 91.0, 90.0, 91.0, 90.0, 91.0, 90.0, 90.0, 90.0, 91.0, 90.0, 91.0, 91.0, 90.0, 90.0, 90.0, 90.0, 90.0, 91.0, 91.0, 92.0, 92.0, 92.0, 91.0, 92.0, 92.0, 93.0, 91.0, 92.0, 91.0, 92.0, 93.0, 91.0, 91.0, 92.0, 91.0, 91.0, 91.0, 91.0, 91.0, 92.0, 91.0, 91.0, 91.0, 90.0, 91.0, 91.0, 93.0, 91.0, 91.0, 91.0, 91.0, 90.0, 90.0, 90.0, 91.0, 91.0, 90.0, 90.0, 89.0, 89.0, 89.0, 90.0, 89.0, 89.0, 89.0, 90.0, 89.0, 88.0, 89.0, 90.0, 89.0, 89.0, 89.0, 90.0, 89.0, 88.0, 89.0, 89.0, 90.0, 89.0, 89.0, 89.0, 89.0, 90.0, 89.0, 89.0, 89.0, 89.0, 90.0, 89.0, 89.0, 89.0, 89.0, 88.0, 90.0, 88.0, 88.0, 88.0, 88.0, 90.0, 88.0, 88.0, 88.0, 88.0, 88.0, 88.0, 88.0, 89.0, 0.0]
Saved wit

In [8]:
import plotly.offline
import plotly.graph_objs as go
import cufflinks
cufflinks.go_offline()

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [9]:
start = 0
points = 1000
try:
    start = plots * points
except:
    plots = 0
# plots = 0

    
res = df.set_index('datetime')
res[start:start+points].iplot(kind='line')

plots = plots +1
# df[].iplot()

In [10]:
# print(list(loads['100_'][0]))
for i in sorted(loads):
    print(i,'has',len(loads[i]),'occurance(s)')
#     for load in loads[i]:
#         if i == '100_':
#             print(round(sum(loads[i][load]['profile'])/360,1),'Wh in ',loads[i][load]['time'])
            


100_ has 85 occurance(s)
1300_ has 2 occurance(s)
1400_ has 1 occurance(s)
1500_ has 2 occurance(s)
1600_ has 7 occurance(s)
1700_ has 10 occurance(s)
1800_ has 6 occurance(s)
1900_ has 1 occurance(s)
2000_ has 7 occurance(s)
200_ has 8 occurance(s)
2100_ has 2 occurance(s)
2600_ has 1 occurance(s)
2700_ has 2 occurance(s)
2800_ has 1 occurance(s)
300_ has 7 occurance(s)
400_ has 13 occurance(s)
500_ has 2 occurance(s)
800_ has 11 occurance(s)
900_ has 3 occurance(s)


In [11]:

res = df.set_index('datetime')
# res[:1000].iplot(kind='line')
# fig = res.plot()
# fig.show()
res.resample('10T').iplot(kind='line')



# res[:100]

/Applications/anaconda/lib/python3.6/site-packages/ipykernel_launcher.py:6: FutureWarning:


.resample() is now a deferred operation
You called iplot(...) on this deferred object which materialized it into a dataframe
by implicitly taking the mean.  Use .resample(...).mean() instead



In [12]:

# df[['datetime',list(loads)]].iplot()
temp = list(loads)
temp[0] = 'datetime'
temp[1] = 'baseload'
temp[2] = 'unknown'

temp[3:] =list(loads)
dp = df[temp]
dp = dp.set_index('datetime')
dp.resample('10T').mean().iplot(kind='line')
# dp.resample('10T').mean().iplot(kind='area',fill='tozeroy',mode='none')



In [13]:
pie = dp.sum()
# values = pie.values/pie.sum()*100
round(pie/pie.sum()*100,1)


baseload    37.8
unknown     35.7
800_         2.9
100_         8.3
900_         0.9
1800_        0.4
300_         0.2
200_         0.1
2000_        5.7
1500_        0.0
1700_        0.4
1400_        0.5
1300_        0.7
2100_        3.3
400_         0.4
2700_        0.5
2600_        0.1
1600_        0.3
500_         0.1
2800_        1.0
1900_        0.8
dtype: float64

In [14]:
trace = go.Pie(labels=pie.index, values=pie.values)
dp.iplot([trace], filename='disaggregator_results_pie')

In [15]:
# import plotly.plotly as py
import plotly.offline as py

trace = go.Pie(labels=pie.index, values=pie.values)

py.plot([trace], filename='disaggregator_results_pie.html')

'file:///Users/arnekaas/Documents/GitHub/disaggregation/disaggregator-deltaPower/disaggregator_results_pie.html'

# Try to rename colums for 'kwown loads' 

In [16]:
#relable output for known_loads
known_loads = {'100_':'Fridge','2000_':'Iron'}
for name in loads.keys():
    try:
        df=df.rename(columns = {name:known_loads[name]})
        loads[known_loads[name]] = loads[name]
    except:
        print(name,'not found known_loads')
    
for name in known_loads:
    try:
        del loads[name]
    except:
        print(name,'not found in legend')

legend = loads.keys()
print(list(legend))

800_ not found known_loads


RuntimeError: dictionary changed size during iteration